# Leigh Ann Kudloff and Nataly Valenzuela Mullen 
# Final Project--Data Science Tools 1  
# Winter 2021

## I.	Introduction/Story
### Like most Data Science students, concern about job opportunities in the near future loom heavily at the halfway point of this degree program.  In one year, employment is necessary to pay off student loans and enter the world of data science.  This project focuses on the world of job hunting in Data Science.  The goal is to explore job descriptions to categorize skill sets, look for patterns, and prepare tools for the job hunt later this year.  Through the exploration of trends in data science job postings, the concepts learned from Data Science Tools 1 and other classes will be applied and hopefully the ideal jobs will emerge.

In [1]:
import itertools
import matplotlib.pyplot as plt
import numpy             as np
import pandas            as pd
import pandas_profiling  as pp
import plotly.express    as px
import re

from mpl_toolkits.mplot3d    import Axes3D
from scipy.cluster.hierarchy import cophenet, dendrogram, linkage
from scipy.spatial.distance  import pdist
from sklearn                 import datasets
from sklearn.cluster         import KMeans
from sklearn.decomposition   import PCA
from sklearn.metrics         import confusion_matrix

In [16]:
df1 = pd.read_csv("DataScienceJobs.csv")

df1 = df1[["Job Title", "Job Description", "Company Name", "City", "State", "Size", 
           "Years_Founded", "Industry", "Rating", "Min_Salary", "Max_Salary", "Est_Salary"]]

strCols = df1.select_dtypes(['object']).columns
df1[strCols] = df1[strCols].apply(lambda x: x.str.strip())

# Used this code to adjust UK jobs for US:  
                                            #df1[df1.State.isin(["United Kingdom"])]
                                            #df1.iloc[1870]["Job Description"]
df1.iloc[1637,3]="Upper Providence"
df1.iloc[1784,3]="Upper Providence"
df1.iloc[1799,3]="Upper Providence"
df1.iloc[1870,3]="Philadelphia"
df1.iloc[[1637, 1784, 1799, 1870], 4]="PA"

# Create Location by joining columns--City and State
df1["Location"]=df1["City"] +", " + df1["State"]

# Creating a column for Remote work
df1.loc[df1["Job Description"].str.contains("Remote|remote"), "Remote"]= "Yes"
df1["Remote"].fillna(value = "Uncertain", axis=0, inplace=True)

# Created bin names for company sizes and used in dataframe
sizeKey = {"1_to_50_employees": "Very Small", 
           "51_to_200_employees": "Small",
          "201_to_500_employees": "Medium-Small",
          "501_to_1000_employees": "Medium",
          "1001_to_5000_employees": "Medium-Large",
          "5001_to_10000_employees": "Large",
          "10000_employees": "Very Large"}
df1["Size"].replace(sizeKey, inplace=True)

df1.rename({"Min_Salary": "SalaryMin", "Max_Salary": "SalaryMax", "Est_Salary": "Salary Estimate"}, 
                  axis=1, inplace=True)

#Changing Years_Founded to Founded
df1["Founded"]=2020-df1["Years_Founded"]
df1.drop(["Years_Founded"], axis=1, inplace=True)

# Removing underscores from Industry
df1["Industry"]=df1["Industry"].replace("_", " ", regex=True)

# Remove duplicate Job listing with same Job Descriptions
criteriaDF1=["Company Name", "Job Title", "City", "State", "SalaryMin", "SalaryMax", "Job Description"]
DF1duplicates=df1[df1.duplicated(criteriaDF1)].sort_values(by=criteriaDF1)
#testDS=DSduplicates.loc[DSduplicates["SalaryMin"].notnull()]
df1=df1[~df1.duplicated(criteriaDF1)]

# Dataframe Label
df1["DF"]= "DF1"

# Reordered Columns for Readability
df1 = df1.reindex(columns = ["Job Title", "Job Description", "Company Name", "Location", "City", "State", "Remote", 
                                             "Size", "Founded", "Industry", "Rating", 
                                             "SalaryMin", "SalaryMax", "Salary Estimate", "DF"])

# Replace "unknown" and "-1" with NaN
df1.replace({"Unknown": np.nan, "-1": np.nan, -1: np.nan}, inplace = True)
#df2["Founded"]=df2["Founded"].astype(int)--We found this did not work well.

print(DF1duplicates.shape)
print(df1.shape)
#df1.head(10)
#df1.State.value_counts()
list(df1.Size.unique())
df1.sample(10)

(21, 14)
(12339, 15)


Job Title  \
2376   Scientist - Immunotherapeutic Design   
1318                  Sr. Data Scientist II   
11781                     Business Analysts   
11102                      Business Analyst   
7279                      Big Data Engineer   
7650              Data Architect / Engineer   
690                           Data Engineer   
8196                   Senior Data Engineer   
7313                    Data Engineer 140K+   
578                 Data Engineer - HBO Max   

                                         Job Description  \
2376   ROLE SUMMARY\nThe Cancer Immunology Discovery ...   
1318   Shutterfly’s purpose is to help share life’s j...   
11781  Opportunity Details\nID: 20747\nTitle: Busines...   
11102  Job Description\nJob Description:-\nProvide re...   
7279   Job Title Big Data Engineer Location Wilmingto...   
7650   Please, no third parties. No sponsorship oppor...   
690    77 West Wacker Dr (35012), United States of Am...   
8196   Job Description\nUnizin is looking for a Senio...   
7313   A local Center City is building out their Data...   
578    Req ID: 178113\nHBO Max is the future of enter...   

                           Company Name          Location          City State  \
2376                             Pfizer      La Jolla, CA      La Jolla    CA   
1318                         Shutterfly         Tempe, AZ         Tempe    AZ   
11781             Convergent Consulting       Fremont, CA       Fremont    CA   
11102  Staffigo Technical Services, LLC     San Diego, CA     San Diego    CA   
7279                             ApTask    Wilmington, DE    Wilmington    DE   
7650                          AbleForce     San Diego, CA     San Diego    CA   
690                         Capital One       Chicago, IL       Chicago    IL   
8196                             Unizin        Austin, TX        Austin    TX   
7313         Management Decisions, Inc.  Philadelphia, PA  Philadelphia    PA   
578                 Turner Broadcasting       Burbank, CA       Burbank    CA   

          Remote          Size  Founded                     Industry  Rating  \
2376   Uncertain    Very Large   1849.0      Biotech Pharmaceuticals     4.1   
1318   Uncertain  Medium-Large   1999.0                     Internet     3.2   
11781  Uncertain    Very Small      NaN                   Consulting     3.9   
11102  Uncertain         Small   2008.0                  IT Services     5.0   
7279   Uncertain  Medium-Small   2010.0                  IT Services     3.9   
7650         Yes           NaN      NaN                          NaN     NaN   
690    Uncertain    Very Large   1994.0          Banks Credit Unions     3.9   
8196   Uncertain    Very Small   2014.0        Colleges Universities     5.0   
7313         Yes    Very Small      NaN        Advertising Marketing     1.6   
578    Uncertain    Very Large   2003.0  TV Broadcast Cable Networks     3.7   

       SalaryMin  SalaryMax  Salary Estimate   DF  
2376          75        149            112.0  DF1  
1318          97        159            128.0  DF1  
11781         63        119             91.0  DF1  
11102         81         97             89.0  DF1  
7279          55        105             80.0  DF1  
7650          79        132            105.5  DF1  
690           46         80             63.0  DF1  
8196          79         96             87.5  DF1  
7313          71        130            100.5  DF1  
578           75        143            109.0  DF1

In [20]:
df2 = pd.read_csv("DataScientist.csv")

df2 = df2[["Job Title", "Job Description", "Company Name", "Location", 
                        "Size", "Founded", "Industry", "Rating", "Salary Estimate"]]

strCols = df2.select_dtypes(['object']).columns
df2[strCols] = df2[strCols].apply(lambda x: x.str.strip())

# Note--Hard coded location changes and used code to determine row numbers of problematic locations:  
# df2[df2.State.isin(["United Kingdom"])]
#print(df2.State.value_counts())
#print(df2[df2.State.isin([" United Kingdom"])])

df2.iloc[1647,3]="Upper Providence, PA"
df2.iloc[1794,3]="Upper Providence, PA"
df2.iloc[1809,3]="Upper Providence, PA"
df2.iloc[1880,3]="Philadelphia, PA"

# Split Location into new columns--City and State
df2[["City", "State"]]= df2["Location"].str.split(",", n = 1, expand = True)
df2.loc[(~df2["Location"].str.contains(",")), "State"]=df2.loc[(~df2["Location"].str.contains(",")),"City"]
df2["State"]=df2["State"].str.strip()
df2.loc[(~df2["Location"].str.contains(",")), "City"]=np.nan

# Creating a column for Remote work and make state nan
df2.loc[(df2["Location"]=="Remote"), "Remote"]="Yes"
df2["Remote"].fillna(value = "Uncertain", axis=0, inplace=True)
df2.loc[(df2["Location"]=="Remote"), "State"]=np.nan

# Creating a column for Remote work
df2.loc[df2["Job Description"].str.contains("Remote|remote"), "Remote"]= "Yes"
df2["Remote"].fillna(value = "Uncertain", axis=0, inplace=True)

# Split Salary Estimate into SalaryMin and SalaryMax and replaced all Salary Estimate with NaN
df2[["SalaryTest", "Salary"]] = df2["Salary Estimate"].str.split("(", n = 1, expand = True)
df2[["SalaryMin", "SalaryMax"]]= df2["SalaryTest"].str.split("-", n = 1, expand = True)
df2.drop(["SalaryTest", "Salary"], axis = 1, inplace = True)
df2["Salary Estimate"] = np.NaN

#Removing the $ and the K from Salary Min and Max
df2["SalaryMin"]=df2["SalaryMin"].replace("[$K]","",regex=True)
df2["SalaryMax"]=df2["SalaryMax"].replace("[$K]","",regex=True)

# Created bin names for company sizes and used in dataframe
sizeKey = {"1 to 50 employees": "Very Small", 
           "51 to 200 employees": "Small",
          "201 to 500 employees": "Medium-Small",
          "501 to 1000 employees": "Medium",
          "1001 to 5000 employees": "Medium-Large",
          "5001 to 10000 employees": "Large",
          "10000+ employees": "Very Large"}
df2["Size"].replace(sizeKey, inplace=True)

# Removed rating from Company Name
df2[["Company Name", "RateTest"]] = df2["Company Name"].str.split("\n", n=1, expand = True)
df2.drop("RateTest", axis = 1, inplace = True)

# Remove duplicate Job listing with same Job Descriptions
criteriaDF2=["Company Name", "Job Title", "City", "State", "SalaryMin", "SalaryMax", "Job Description"]
DF2duplicates=df2[df2.duplicated(criteriaDF2)].sort_values(by=criteriaDF2)
#testDS=DSduplicates.loc[DSduplicates["SalaryMin"].notnull()]
df2=df2[~df2.duplicated(criteriaDF2)]

# Dataframe Label
df2["DF"]= "DF2"

# Reordered Columns for Readability
df2 = df2.reindex(columns = ["Job Title", "Job Description", "Company Name", "Location", "City", "State", "Remote",
                              "Size", "Founded", "Industry", "Rating", "SalaryMin", "SalaryMax", "Salary Estimate", "DF"])

# Replace "unknown" and "-1" with NaN
df2.replace({"Unknown": np.nan, "-1": np.nan, -1: np.nan}, inplace = True)
#df2["Founded"]=df2["Founded"].astype(int)--We found this did not work well.

#print(DF2duplicates.shape)
print(df2.shape)
df2.sample(10)

(0, 14)
(3909, 15)


Job Title  \
1351  Internship - Analytics and Data Science (Healt...   
1090                                 Physical Scientist   
1858                                       Sr Scientist   
3052                                       Data Analyst   
3594                                  Data Architect II   
3441                                Data Analyst Junior   
213   Software Engineer - Data Engineering, Finance ...   
3105                                       Data Analyst   
2483                                    Data Analyst II   
3854  Post Doctoral Scientist Year 1-3 RI Mathematic...   

                                        Job Description  \
1351  Blue Cross Blue Shield of Arizona is a local, ...   
1090  The Department of Energy is seeking motivated ...   
1858  Site Name: USA - Pennsylvania - King of Prussi...   
3052  KAYGEN is an emerging leader in providing top ...   
3594  Job Description\nON BOARD SERVICES\nHiring a C...   
3441  Job Description\nJob description\nInterpret da...   
213   As a member of our Data Engineering team, you’...   
3105  PETADATA is looking for a Data Analyst to work...   
2483  The Data Analyst II is responsible for data en...   
3854  JOB POSTING – Post Doctoral Scientist Year 1-3...   

                           Company Name             Location             City  \
1351  Blue Cross Blue Shield of Arizona          Phoenix, AZ          Phoenix   
1090            US Department of Energy          Houston, TX          Houston   
1858                                GSK  King of Prussia, PA  King of Prussia   
3052                        Kaygen Inc.         San Jose, CA         San Jose   
3594                 On-Board Companies     Jacksonville, FL     Jacksonville   
3441   Staffigo Technical Services, LLC           Austin, TX           Austin   
213                         Squarespace         New York, NY         New York   
3105                           PETADATA         San Jose, CA         San Jose   
2483          Insight Enterprises, Inc.            Plano, TX            Plano   
3854     Nationwide Children's Hospital         Columbus, OH         Columbus   

     State     Remote          Size  Founded  \
1351    AZ  Uncertain  Medium-Large   1939.0   
1090    TX  Uncertain    Very Large   1977.0   
1858    PA  Uncertain    Very Large   1830.0   
3052    CA  Uncertain    Very Small      NaN   
3594    FL  Uncertain  Medium-Large   1976.0   
3441    TX  Uncertain         Small   2008.0   
213     NY  Uncertain  Medium-Large   2003.0   
3105    CA  Uncertain         Small      NaN   
2483    TX  Uncertain         Large   1988.0   
3854    OH  Uncertain    Very Large   1892.0   

                                     Industry  Rating SalaryMin SalaryMax  \
1351                       Insurance Carriers     3.1        97      159    
1090                         Federal Agencies     3.6        39       87    
1858                Biotech & Pharmaceuticals     3.9       143      237    
3052                               Consulting     3.9       119      188    
3594                               Consulting     3.4        61       94    
3441                              IT Services     5.0        74      144    
213                                  Internet     3.4       119      147    
3105                                      NaN     NaN       150      169    
2483  Enterprise Software & Network Solutions     4.0        12      112    
3854         Health Care Services & Hospitals     3.7        39       86    

      Salary Estimate   DF  
1351              NaN  DF2  
1090              NaN  DF2  
1858              NaN  DF2  
3052              NaN  DF2  
3594              NaN  DF2  
3441              NaN  DF2  
213               NaN  DF2  
3105              NaN  DF2  
2483              NaN  DF2  
3854              NaN  DF2

In [5]:
# column selection--unnecessary columns eliminated
dfGlassdoor = pd.read_csv("glassdoor_jobs.csv")
# print(list(dfGlassdoor.columns))
dfGlassdoor.drop(['Headquarters', 'Sector', 'Revenue', 'Competitors', 'Type of ownership'],axis = 1, inplace = True)

strCols = dfGlassdoor.select_dtypes(['object']).columns
dfGlassdoor[strCols] = dfGlassdoor[strCols].apply(lambda x: x.str.strip())

# Note--Hard coded location changes and used code to determine row numbers of problematic locations:  
# dfGlassdoor[dfGlassdoor.State.isin (["None", " Raleigh", " Anne Arundel, MD"])])

dfGlassdoor.iloc[297,5]="Patuxent, MD"
dfGlassdoor.iloc[136,5]="Raleigh, NC"
dfGlassdoor.iloc[320,5]="Remote"
dfGlassdoor.iloc[12,5]="Portland, OR"
dfGlassdoor.iloc[157,5]="Chicago, IL"
dfGlassdoor.iloc[163,5]="Pembroke Pines, Florida"
dfGlassdoor.iloc[11,5]="Holmdel, NJ"
dfGlassdoor.iloc[346,5]="Middlesex, NJ"
dfGlassdoor.iloc[757,5]="Arlington, VA"
dfGlassdoor.iloc[758,5]="Hollywood, CA"
dfGlassdoor.iloc[830,5]="Washington, DC"

# Split Location into new columns--City and State and make city nan
dfGlassdoor[["City", "State"]]= dfGlassdoor["Location"].str.split(",", n = 1, expand = True)
dfGlassdoor.loc[(~dfGlassdoor["Location"].str.contains(",")), "State"]=dfGlassdoor.loc[(~dfGlassdoor["Location"].str.contains(",")),"City"]
dfGlassdoor["State"]=dfGlassdoor["State"].str.strip()
dfGlassdoor.loc[(~dfGlassdoor["Location"].str.contains(",")), "City"]=np.nan

# Creating a column for Remote work and make state nan
dfGlassdoor.loc[(dfGlassdoor["Location"]=="Remote"), "Remote"]="Yes"
dfGlassdoor["Remote"].fillna(value = "Uncertain", axis=0, inplace=True)
dfGlassdoor.loc[(dfGlassdoor["Location"]=="Remote"), "State"]=np.nan

# Adding to column for Remote work from Job Description
dfGlassdoor.loc[dfGlassdoor["Job Description"].str.contains("Remote|remote"), "Remote"]= "Yes"

# Split Salary Estimate into SalaryMin and SalaryMax and replaced all Salary Estimate with NaN
dfGlassdoor[["SalaryTest", "Salary"]] = dfGlassdoor["Salary Estimate"].str.split("(", n = 1, expand = True)
dfGlassdoor[["SalaryMin", "SalaryMax"]]= dfGlassdoor["SalaryTest"].str.split("-", n = 1, expand = True)
dfGlassdoor.drop(["SalaryTest", "Salary"], axis = 1, inplace = True)
dfGlassdoor["Salary Estimate"] = np.NaN

#Removing the $ and the K from Salary Min and Max
dfGlassdoor["SalaryMin"]=dfGlassdoor["SalaryMin"].replace("[$K]","",regex=True)
dfGlassdoor["SalaryMax"]=dfGlassdoor["SalaryMax"].replace("[$K]","",regex=True)

# Created bin names for company sizes and used in dataframe
sizeKey = {"1 to 50 employees": "Very Small", 
           "51 to 200 employees": "Small",
          "201 to 500 employees": "Medium-Small",
          "501 to 1000 employees": "Medium",
          "1001 to 5000 employees": "Medium-Large",
          "5001 to 10000 employees": "Large",
          "10000+ employees": "Very Large"}
dfGlassdoor["Size"].replace(sizeKey, inplace=True)

# Removed rating from Company Name
dfGlassdoor[["Company Name", "RateTest"]] = dfGlassdoor["Company Name"].str.split("\n", n=1, expand = True)
dfGlassdoor.drop("RateTest", axis = 1, inplace = True)

# Remove duplicate Job listing with same Job Descriptions
criteriaGD=["Company Name", "Job Title", "City", "State", "SalaryMin", "SalaryMax", "Job Description"]
#GDduplicates=dfGlassdoor[dfGlassdoor.duplicated(criteriaGD)].sort_values(by=criteriaGD)
#testGD=GDduplicates.loc[GDduplicates["SalaryMin"].notnull()]
dfGlassdoor=dfGlassdoor[~dfGlassdoor.duplicated(criteriaGD)]

# Dataframe Label
dfGlassdoor["DF"]= "GD"

# Reordered Columns for Readability
dfGlassdoor = dfGlassdoor.reindex(columns = ["Job Title", "Job Description", "Company Name", "Location", "City", "State", 
                                             "Remote", "Size", "Founded", "Industry", "Rating", 
                                             "SalaryMin", "SalaryMax", "Salary Estimate", "DF"])

# Replace "unknown" and "-1" with NaN
dfGlassdoor.replace({"Unknown": np.nan, "-1": np.nan, -1: np.nan}, inplace = True)
dfGlassdoor.fillna(value=np.nan, axis=1, inplace=True)
#dfGlassdoor["Founded"]=dfGlassdoor["Founded"].astype(int)--We found this did not work well.

#print(testGD.shape)
print(dfGlassdoor.shape)
dfGlassdoor.sample(20)


(899, 15)


Job Title  \
283                           Data Scientist Architect   
799                        Medical Lab Scientist (MLS)   
854                                     Data Scientist   
327                                 Lead Data Engineer   
468                                     Data Scientist   
179  Temporary Assignment - Clinical Laboratory Sci...   
467                                     Data Scientist   
376                    Senior Insurance Data Scientist   
188                       Data Scientist active TS/SCI   
710                                     Data Scientist   
279                                     Data Scientist   
590                                     Data Scientist   
277  Sr./Scientist, Computational Chemistry/Cheminf...   
556                                     Data Scientist   
809                                     Data Scientist   
583                                     Data Scientist   
244                                    Sr Data Analyst   
437                                     Data Scientist   
359                                     Data Scientist   
662                                     Data Scientist   

                                       Job Description  \
283  This career opportunity is in our Minneapolis ...   
799  We Are Hiring\n\nMedical Lab Scientist (MLS) -...   
854  Get in on the ground floor at one of Boston's ...   
327  1 Broadway (21026), United States of America, ...   
468  Schrödinger’s mission is to revolutionize drug...   
179  The Clinical Laboratory Scientist I performs l...   
467  Job Description\nGalorath Federal is a growing...   
376  What We'll Bring:\n\nAt TransUnion, we have a ...   
188  We are currently seeking an innovative, experi...   
710  Role Description\nAs a data scientist at Tripl...   
279  Job Duties & Responsibilities\nBring Creativit...   
590  Meridian Knowledge Solutions, LLC, is the lead...   
277  The Role:\nModerna is seeking a talented and m...   
556  Job Description\nGreetings from Avtech Solutio...   
809  At Wish, our Data Science & Engineering team i...   
583  Title Data Scientist Position Type Right to Hi...   
244  Position location: Lake Mary, FLorBlue Bell, P...   
437  We have an exciting opportunity for a Seals Pr...   
359  Hello Associates,\n\n*****Greetings from Conch...   
662  Position: Data Scientist\n\nLocation: Washingt...   

                           Company Name            Location            City  \
283                      SullivanCotter     Minneapolis, MN     Minneapolis   
799  Sacred Heart Hospital of Pensacola     Panama City, FL     Panama City   
854                           LogRocket          Boston, MA          Boston   
327                         Capital One       Cambridge, MA       Cambridge   
468                         Schrödinger        Portland, OR        Portland   
179          Exact Sciences Corporation         Madison, WI         Madison   
467                       Galorath Inc.      Charleston, SC      Charleston   
376                          TransUnion         Chicago, IL         Chicago   
188                                 LMI    Fort Belvoir, VA    Fort Belvoir   
710                          Triplebyte   San Francisco, CA   San Francisco   
279                           BlackLine  Woodland Hills, CA  Woodland Hills   
590        Meridian Knowledge Solutions      Washington, DC      Washington   
277                Moderna Therapeutics       Cambridge, MA       Cambridge   
556                    Avtech solutions      Great Neck, NY      Great Neck   
809                                Wish         Seattle, WA         Seattle   
583    HALLMARK GLOBAL TECHNOLOGIES INC         Phoenix, AZ         Phoenix   
244                    United BioSource       Blue Bell, PA       Blue Bell   
437                         Amsted Rail    Granite City, IL    Granite City   
359             Conch Technologies, Inc         Concord, CA         Concord   
662                        

In [23]:
dfIndeed = pd.read_csv("df_all_indeed.csv")

dfIndeed.drop(['Unnamed: 0','Easy_Apply'],axis = 1, inplace = True)

strCols = dfIndeed.select_dtypes(['object']).columns
dfIndeed[strCols] = dfIndeed[strCols].apply(lambda x: x.str.strip())

dfIndeed.iloc[[57, 114, 231,3521,3632,3637,3961],2]="Carlsbad, NM"
dfIndeed.iloc[[3520, 3578, 3661,3666,3776, 3843, 3967],2]="Spring, TX"
dfIndeed.iloc[3772, 2]="Panama City, FL"
dfIndeed.iloc[[1607, 1765, 1801],2]="New York, NY"
dfIndeed.iloc[[557, 665],2]="Remote"
dfIndeed.iloc[[410,1484],2]="San Diego, CA"
dfIndeed.iloc[418, 2]="Los Angelos, CA"
dfIndeed.iloc[82, 2]="Denver, CO"
dfIndeed.iloc[[1009, 1327],2]="Menlo Park, CA"

dfIndeed[["City", "State"]]= dfIndeed["Locations"].str.split(",", n = 1, expand = True)
dfIndeed.loc[(~dfIndeed["Locations"].str.contains(",")), "State"]=dfIndeed.loc[(~dfIndeed["Locations"].str.contains(",")),"City"]
dfIndeed.loc[(~dfIndeed["Locations"].str.contains(",")), "City"]=np.nan

# Creating a column for Remote work and make state nan
dfIndeed.loc[(dfIndeed["Locations"]=="Remote"), "Remote"]="Yes"
dfIndeed["Remote"].fillna(value = "Uncertain", axis=0, inplace=True)
dfIndeed.loc[(dfIndeed["Locations"]=="Remote"), "State"]=np.nan

# Adding to column for Remote work from Job Description
dfIndeed.loc[(dfIndeed["Summary"].str.contains("Remote|remote")==True), "Remote"]= "Yes"
dfIndeed.loc[(dfIndeed["Jobs"].str.contains("Remote|remote")==True), "Remote"]= "Yes"

dfIndeed.rename({"Summary": "Job Description", "Companies": "Company Name", "Jobs": "Job Title", "Locations": "Location"}, 
                  axis=1, inplace=True)

# Remove duplicate Job listing with same Job Descriptions
criteriaIN=["Company Name", "Job Title", "City", "State", "Job Description"]
INduplicates=dfIndeed[dfIndeed.duplicated(criteriaIN)].sort_values(by=criteriaIN)
#testDS=DSduplicates.loc[DSduplicates["SalaryMin"].notnull()]
dfIndeed=dfIndeed[~dfIndeed.duplicated(criteriaIN)]

# Dataframe Label
dfIndeed["DF"]= "IN"

# Reordered Columns for Readability
dfIndeed = dfIndeed.reindex(columns = ["Job Title", "Job Description", "Company Name", 
                                       "Location", "City", "State", "Remote", "Rating", "DF"])
#print(INduplicates.shape)
print(dfIndeed.shape)
dfIndeed.head(10)

(1098, 8)
(2871, 9)


Job Title  \
0                               Data Science Modeler   
1                   Director Integrated Data Science   
2                                     Data Scientist   
3                                     Data Scientist   
4               Sr Business Analyst / Data Scientist   
5                                      Data Engineer   
6                                     Data Scientist   
7                                     Data Scientist   
8                               Data Science Analyst   
9  Senior Applications Scientist, Bioinformatics/...   

                                     Job Description          Company Name  \
0  As a Data Science Modeler, you will be a key p...                 Avero   
1  Demonstrated knowledge of programming expertis...                  UPMC   
2  University bachelor’s degree in data science, ...  Willis Towers Watson   
3  Effectively represent the Data Science group i...       Valen Analytics   
4  See the data “forest for the trees” and help i...               PHOENIX   
5  Troubleshoot basic data and data engineering i...       Valen Analytics   
6  Data scientists use data and analytical abilit...            Horizontal   
7  Data Science: 3 years (Preferred). Data scient...             Pricesenz   
8  Data Engineer Tech – :Cleaning and Integrating...   xentity corporation   
9  Expertise in probability & statistics, machine...             Inscripta   

         Location        City State     Remote  Rating  DF  
0     Boulder, CO     Boulder    CO  Uncertain     2.6  IN  
1    Loveland, CO    Loveland    CO  Uncertain     3.7  IN  
2      Denver, CO      Denver    CO  Uncertain     3.7  IN  
3      Denver, CO      Denver    CO  Uncertain     NaN  IN  
4      Denver, CO      Denver    CO  Uncertain     NaN  IN  
5      Denver, CO      Denver    CO  Uncertain     NaN  IN  
6  Broomfield, CO  Broomfield    CO  Uncertain     NaN  IN  
7  Broomfield, CO  Broomfield    CO  Uncertain     NaN  IN  
8      Denver, CO      Denver    CO  Uncertain     4.6  IN  
9     Boulder, CO     Boulder    CO  Uncertain     3.0  IN

In [29]:
dfLinkedIn = pd.read_csv("df_all_linkedin.csv")

dfLinkedIn.drop(['Unnamed: 0','Number_of_Applicants', 'Length_of_Description', 'num_applicants'],axis = 1, inplace = True)

#This strips unnecessary white spaces.
strCols = dfLinkedIn.select_dtypes(['object']).columns
dfLinkedIn[strCols] = dfLinkedIn[strCols].apply(lambda x: x.str.strip())

#This code was used to clean up city names and areas.
#for i, s in enumerate(dfLinkedIn['Location']):
#    if not s.endswith(', US') and not s.endswith(', United States'):
#        print(i, s)

cities = {'Greater Denver Area':              'Denver',
          'San Francisco Bay Area':           'San Francisco',
          'Greater Los Angeles Area':         'Los Angeles',
          'Greater New York City Area':       'New York City',
          'New York City Metropolitan Area':  'New York City',
          'Greater Seattle Area':             'Seattle',
          'Salt Lake City Metropolitan Area': 'Salt Lake City',
          'Miami/Fort Lauderdale Area':       'Miami'}

# Separates the location into City column and throws away the state and US info
dfLinkedIn[["City", "Temp"]] = dfLinkedIn["Location"].str.split(",", 1, expand = True)
dfLinkedIn.drop("Temp", axis = 1, inplace = True)
dfLinkedIn["City"].replace(cities, inplace=True)
dfLinkedIn["Location"]=dfLinkedIn["City"]+", "+ dfLinkedIn["State"]

# Adding to column for Remote work from Job Description
dfLinkedIn.loc[dfLinkedIn["Description"].str.contains("Remote|remote"), "Remote"]= "Yes"
dfLinkedIn["Remote"].fillna(value = "Uncertain", axis=0, inplace=True)

dfLinkedIn.rename({"Description": "Job Description", "Company": "Company Name", "Job_Title": "Job Title"}, 
                  axis=1, inplace=True)

# Remove duplicate Job listing with same Job Descriptions
criteriaLI=["Company Name", "Job Title", "City", "State", "Junior", "Senior", "Job Description"]
LIduplicates=dfLinkedIn[dfLinkedIn.duplicated(criteriaLI)].sort_values(by=criteriaLI)
#testDS=DSduplicates.loc[DSduplicates["SalaryMin"].notnull()]
dfLinkedIn=dfLinkedIn[~dfLinkedIn.duplicated(criteriaLI)]

# Dataframe Label
dfLinkedIn["DF"]= "LI"

# Reordered Columns for Readability
dfLinkedIn = dfLinkedIn.reindex(columns = ["Job Title", "Job Description", "Company Name", "Location", "City", "State", 
                                             "Remote", "Junior", "Senior", "DF"])
#print(LIduplicates.shape)
#print(dfLinkedIn.head())
print(dfLinkedIn.shape)
dfLinkedIn.head(10)

(1794, 10)
(1356, 10)


Job Title  \
0                         Data Acquisition Developer   
1                             DATA SCIENTIST MANAGER   
2  Data Scientist – Logistics Optimization Algori...   
3  Senior Director - Global Data & Analytics Arch...   
4  Senior Consultant - Professional Services (Rem...   
5                                     Data Scientist   
6                     Data Scientist I - 2020 Campus   
7                                      Data Engineer   
8                                      Data Engineer   
9                          Marketing Science Analyst   

                                     Job Description            Company Name  \
0  Join ABB and work in a team that is dedicated ...                     ABB   
1  Pilgrim’s is the second largest chicken produc...               Pilgrim's   
2  Location: Denver, CO – Relocation Offered. Rem...               ShaleApps   
3  VF Corporation outfits consumers around the wo...          VF Corporation   
4  Who We AreTalend is a leader in cloud data int...                  Talend   
5  Job FamilyAdvanced AnalyticsJob Description Su...  Aegon Asset Management   
6  This is a talent pipeline requisition for coll...              Travelport   
7  Job Description Apply proven expertise and bui...           Fahrenheit IT   
8  Data Engineer – Denver, Colorado Want to work ...           Western Union   
9  OverviewAnalytic Partners is looking for a Mar...       Analytic Partners   

         Location        City State     Remote  Junior  Senior  DF  
0  Broomfield, CO  Broomfield    CO  Uncertain       0       0  LI  
1     Greeley, CO     Greeley    CO  Uncertain       0       0  LI  
2      Denver, CO      Denver    CO        Yes       0       0  LI  
3      Denver, CO      Denver    CO        Yes       0       1  LI  
4      Denver, CO      Denver    CO  Uncertain       0       1  LI  
5      Denver, CO      Denver    CO  Uncertain       0       0  LI  
6   Englewood, CO   Englewood    CO  Uncertain       0       0  LI  
7      Denver, CO      Denver    CO  Uncertain       0       0  LI  
8      Denver, CO      Denver    CO  Uncertain       0       0  LI  
9      Denver, CO      Denver    CO  Uncertain       0       0  LI

In [8]:
dfDataAnalyst = pd.read_csv("DataAnalyst.csv")

dfDataAnalyst = dfDataAnalyst[["Job Title", "Job Description", "Company Name", "Location", 
                        "Size", "Founded", "Industry", "Rating", "Salary Estimate"]]

strCols = dfDataAnalyst.select_dtypes(['object']).columns
dfDataAnalyst[strCols] = dfDataAnalyst[strCols].apply(lambda x: x.str.strip())

# Split Location into new columns--City and State and make city nan
dfDataAnalyst[["City", "State"]]= dfDataAnalyst["Location"].str.split(",", n = 1, expand = True)
dfDataAnalyst.loc[(~dfDataAnalyst["Location"].str.contains(",")), "State"]=dfDataAnalyst.loc[(~dfDataAnalyst["Location"].str.contains(",")),"City"]
dfDataAnalyst["State"]=dfDataAnalyst["State"].str.strip()
dfDataAnalyst.loc[(~dfDataAnalyst["Location"].str.contains(",")), "City"]=np.nan

#dfDataAnalyst=dfDataAnalyst.loc[(dfDataAnalyst["State"]=="Arapahoe, CO")]
dfDataAnalyst.loc[(dfDataAnalyst["State"].str.contains("Arapahoe, CO")),"State"]="CO"

# Creating a column for Remote work and make state nan
dfDataAnalyst.loc[(dfDataAnalyst["Location"]=="Remote"), "Remote"]="Yes"
dfDataAnalyst["Remote"].fillna(value = "Uncertain", axis=0, inplace=True)
dfDataAnalyst.loc[(dfDataAnalyst["Location"]=="Remote"), "State"]=np.nan

# Adding to column for Remote work from Job Description
dfDataAnalyst.loc[dfDataAnalyst["Job Description"].str.contains("Remote|remote"), "Remote"]= "Yes"

# Split Salary Estimate into SalaryMin and SalaryMax and replaced all Salary Estimate with NaN
dfDataAnalyst[["SalaryTest", "Salary"]] = dfDataAnalyst["Salary Estimate"].str.split("(", n = 1, expand = True)
dfDataAnalyst[["SalaryMin", "SalaryMax"]]= dfDataAnalyst["SalaryTest"].str.split("-", n = 1, expand = True)
dfDataAnalyst.drop(["SalaryTest", "Salary"], axis = 1, inplace = True)
dfDataAnalyst["Salary Estimate"] = np.NaN

#Removing the $ and the K from Salary Min and Max
dfDataAnalyst["SalaryMin"]=dfDataAnalyst["SalaryMin"].replace("[$K]","",regex=True)
dfDataAnalyst["SalaryMax"]=dfDataAnalyst["SalaryMax"].replace("[$K]","",regex=True)

# Created bin names for company sizes and used in dataframe
sizeKey = {"1 to 50 employees": "Very Small", 
           "51 to 200 employees": "Small",
          "201 to 500 employees": "Medium-Small",
          "501 to 1000 employees": "Medium",
          "1001 to 5000 employees": "Medium-Large",
          "5001 to 10000 employees": "Large",
          "10000+ employees": "Very Large"}
dfDataAnalyst["Size"].replace(sizeKey, inplace=True)

# Removed rating from Company Name
dfDataAnalyst[["Company Name", "RateTest"]] = dfDataAnalyst["Company Name"].str.split("\n", n=1, expand = True)
dfDataAnalyst.drop("RateTest", axis = 1, inplace = True)

# Remove duplicate Job listing with same Job Descriptions
criteriaDA=["Company Name", "Job Title", "City", "State", "SalaryMin", "SalaryMax", "Job Description"]
#DAduplicates=dfDataAnalyst[dfDataAnalyst.duplicated(criteriaDA)].sort_values(by=criteriaDA)
#testDA=DAduplicates.loc[DAduplicates["SalaryMin"].notnull()]
dfDataAnalyst=dfDataAnalyst[~dfDataAnalyst.duplicated(criteriaDA)]

# Dataframe Label
dfDataAnalyst["DF"]= "DA"

# Reordered Columns for Readability
dfDataAnalyst = dfDataAnalyst.reindex(columns = ["Job Title", "Job Description", "Company Name", "Location", "City", "State", 
                                             "Remote", "Size", "Founded", "Industry", "Rating", 
                                             "SalaryMin", "SalaryMax", "Salary Estimate", "DF"])

# Replace "unknown" and "-1" with NaN
dfDataAnalyst.replace({"Unknown": np.nan, "-1": np.nan, -1: np.nan}, inplace = True)
dfDataAnalyst.fillna(value=np.nan, axis=1, inplace=True)

#print(testDA.shape)
print(dfDataAnalyst.shape)
dfDataAnalyst.sample(10)

(2253, 15)


Job Title  \
1672  TSDS Data QA Analyst (Data Analyst IV)   
1712                     Senior Data Analyst   
1067               Data Analyst - Priceguide   
1649  Business Intelligence and Data Analyst   
2198         Data Analyst- Growth Operations   
1530            Maps Evaluation Data Analyst   
1960                            Data Analyst   
1471                            Data Analyst   
1181      Sr. Data Analyst - Project Manager   
1490                            Data Analyst   

                                        Job Description  \
1672  TSDS Data QA Analyst (Data Analyst IV) (000100...   
1712  Job Description\n\nThe Senior Data Analyst is ...   
1067  Data Analyst - Priceguide\n\nJob Details\nLeve...   
1649  The Business Intelligence and Data Analyst per...   
2198  Job Description\nRxRevu is hiring a mid-level ...   
1530  Posted: Jun 29, 2020\nWeekly Hours: 40\nRole N...   
1960  Summary:\n\nThe Marin City Health and Wellness...   
1471  As the leader in Lead-to-Account Matching, Rou...   
1181  We are seeking a Sr. Analyst/PM to work for a ...   
1490  Zipongo sits at the forefront of how we eat, m...   

                               Company Name              Location  \
1672                 TEXAS EDUCATION AGENCY            Austin, TX   
1712                        Iris Plans Inc.            Austin, TX   
1067                                   ECRI  Plymouth Meeting, PA   
1649     Teacher Retirement System of Texas            Austin, TX   
2198                                 RxRevu            Denver, CO   
1530                                  Apple       Santa Clara, CA   
1960  Marin City Health and Wellness Center        Marin City, CA   
1471                               LeanData       Santa Clara, CA   
1181                                TechUSA      Philadelphia, PA   
1490                                Zipongo          San Jose, CA   

                  City State     Remote          Size  Founded  \
1672            Austin    TX  Uncertain        Medium      NaN   
1712            Austin    TX        Yes    Very Small      NaN   
1067  Plymouth Meeting    PA  Uncertain  Medium-Small   1968.0   
1649            Austin    TX  Uncertain        Medium   1937.0   
2198            Denver    CO  Uncertain    Very Small      NaN   
1530       Santa Clara    CA  Uncertain    Very Large   1976.0   
1960        Marin City    CA  Uncertain    Very Small   2007.0   
1471       Santa Clara    CA  Uncertain         Small   2012.0   
1181      Philadelphia    PA  Uncertain  Medium-Large   1998.0   
1490          San Jose    CA  Uncertain         Small   2011.0   

                                     Industry  Rating SalaryMin SalaryMax  \
1672                State & Regional Agencies     2.8        53      104    
1712                                      NaN     NaN        35       42    
1067         Health Care Services & Hospitals     3.6        41       78    
1649    Investment Banking & Asset Management     3.9        42       76    
2198         Health Care Services & Hospitals     3.0        49       91    
1530             Computer Hardware & Software     4.1        69      127    
1960         Health Care Services & Hospitals     4.5        93      159    
1471  Enterprise Software & Network Solutions     4.0       110      190    
1181                   Staffing & Outsourcing     2.7        64      113    
1490         Health Care Services & Hospitals     4.0       110      190    

      Salary Estimate  DF  
1672              NaN  DA  
1712              NaN  DA  
1067              NaN  DA  
1649              NaN  DA  
2198              NaN  DA  
1530              NaN  DA  
1960              NaN  DA  
1471              NaN  DA  
1181              NaN  DA  
1490              NaN  DA

In [9]:
dfDataEngineer = pd.read_csv("DataEngineer.csv")

dfDataEngineer = dfDataEngineer[["Job Title", "Job Description", "Company Name", "Location", 
                        "Size", "Founded", "Industry", "Rating", "Salary Estimate"]]

strCols = dfDataEngineer.select_dtypes(['object']).columns
dfDataEngineer[strCols] = dfDataEngineer[strCols].apply(lambda x: x.str.strip())

# Split Location into new columns--City and State and make city nan
dfDataEngineer[["City", "State"]]= dfDataEngineer["Location"].str.split(",", n = 1, expand = True)
dfDataEngineer.loc[(~dfDataEngineer["Location"].str.contains(",")), "State"]=dfDataEngineer.loc[(~dfDataEngineer["Location"].str.contains(",")),"City"]
dfDataEngineer["State"]=dfDataEngineer["State"].str.strip()
dfDataEngineer.loc[(~dfDataEngineer["Location"].str.contains(",")), "City"]=np.nan

# Creating a column for Remote work and make state nan
dfDataEngineer.loc[(dfDataEngineer["Location"]=="Remote"), "Remote"]="Yes"
dfDataEngineer["Remote"].fillna(value = "Uncertain", axis=0, inplace=True)
dfDataEngineer.loc[(dfDataEngineer["Location"]=="Remote"), "State"]=np.nan

# Adding to column for Remote work from Job Description
dfDataEngineer.loc[dfDataEngineer["Job Description"].str.contains("Remote|remote"), "Remote"]= "Yes"

# Split Salary Estimate into SalaryMin and SalaryMax and replaced all Salary Estimate with NaN
dfDataEngineer[["SalaryTest", "Salary"]] = dfDataEngineer["Salary Estimate"].str.split("(", n = 1, expand = True)
dfDataEngineer[["SalaryMin", "SalaryMax"]]= dfDataEngineer["SalaryTest"].str.split("-", n = 1, expand = True)
dfDataEngineer.drop(["SalaryTest", "Salary"], axis = 1, inplace = True)
dfDataEngineer["Salary Estimate"] = np.NaN

#Removing the $ and the K from Salary Min and Max
dfDataEngineer["SalaryMin"]=dfDataEngineer["SalaryMin"].replace("[$K]","",regex=True)
dfDataEngineer["SalaryMax"]=dfDataEngineer["SalaryMax"].replace("[$K]","",regex=True)

# Created bin names for company sizes and used in dataframe
sizeKey = {"1 to 50 employees": "Very Small", 
           "51 to 200 employees": "Small",
          "201 to 500 employees": "Medium-Small",
          "501 to 1000 employees": "Medium",
          "1001 to 5000 employees": "Medium-Large",
          "5001 to 10000 employees": "Large",
          "10000+ employees": "Very Large"}
dfDataEngineer["Size"].replace(sizeKey, inplace=True)

# Removed rating from Company Name
dfDataEngineer[["Company Name", "RateTest"]] = dfDataEngineer["Company Name"].str.split("\n", n=1, expand = True)
dfDataEngineer.drop("RateTest", axis = 1, inplace = True)

# Remove duplicate Job listing with same Job Descriptions
criteriaDE=["Company Name", "Job Title", "City", "State", "SalaryMin", "SalaryMax", "Job Description"]
#DEduplicates=dfDataEngineer[dfDataEngineer.duplicated(criteriaDE)].sort_values(by=criteriaDE)
#testDE=DEduplicates.loc[DEduplicates["SalaryMin"].notnull()]
dfDataEngineer=dfDataEngineer[~dfDataEngineer.duplicated(criteriaDE)]

# Dataframe Label
dfDataEngineer["DF"]= "DE"

# Reordered Columns for Readability
dfDataEngineer = dfDataEngineer.reindex(columns = ["Job Title", "Job Description", "Company Name", "Location", "City", "State", 
                                             "Remote", "Size", "Founded", "Industry", "Rating", 
                                             "SalaryMin", "SalaryMax", "Salary Estimate", "DF"])

# Replace "unknown" and "-1" with NaN
dfDataEngineer.replace({"Unknown": np.nan, "-1": np.nan, -1: np.nan}, inplace = True)
dfDataEngineer.fillna(value=np.nan, axis=1, inplace=True)

#print(testDE.shape)
print(dfDataEngineer.shape)
dfDataEngineer.sample(10)

(2516, 15)


Job Title  \
400               Tableau Data Engineer 20-0117   
193                               Data Engineer   
2098                  Machine Learning Engineer   
2431                    Principal data engineer   
880   (Project Staff) Consultant, Data Engineer   
292                        Senior Data Engineer   
105                               Data Engineer   
293                        Senior Data Engineer   
1944                              Data Engineer   
377                         Azure Data Engineer   

                                        Job Description  \
400   We are Relativity. A market-leading, global te...   
193   Job Description\n\n\nJob #: 1076197\n\nTitle- ...   
2098  ABOUT ENVIEW\n\nEnview creates a digital twin ...   
2431  Job SummaryJoin the team that powers the globa...   
880   As a team member in the Finance and Internal A...   
292   Our company is looking for a Senior Data Engin...   
105   FanDuel Group is an innovative sports-tech ent...   
293   Job Description\nThis is a 100% Remote positio...   
1944  Work Authorization Those authorized to work in...   
377   AWS Data Engineer for my client, Petco, in San...   

                   Company Name         Location         City State  \
400                  Relativity      Chicago, IL      Chicago    IL   
193                Apex Systems     New York, NY     New York    NY   
2098                     Enview       Austin, TX       Austin    TX   
2431                  CoreLogic       Irving, TX       Irving    TX   
880                  Nationwide   Scottsdale, AZ   Scottsdale    AZ   
292                    Evolvinc      Burbank, CA      Burbank    CA   
105                     FanDuel     New York, NY     New York    NY   
293   RennickBarrett Recruiting  Los Angeles, CA  Los Angeles    CA   
1944                   PETADATA      Fremont, CA      Fremont    CA   
377    System Soft Technologies     Cerritos, CA     Cerritos    CA   

         Remote          Size  Founded  \
400   Uncertain  Medium-Large   2001.0   
193   Uncertain  Medium-Large   1995.0   
2098  Uncertain    Very Small   2015.0   
2431  Uncertain         Large   2010.0   
880   Uncertain    Very Large   1925.0   
292   Uncertain    Very Small   2005.0   
105   Uncertain        Medium   2009.0   
293         Yes           NaN      NaN   
1944  Uncertain         Small      NaN   
377   Uncertain  Medium-Small   1999.0   

                                     Industry  Rating SalaryMin SalaryMax  \
400   Enterprise Software & Network Solutions     3.7        56      108    
193                    Staffing & Outsourcing     3.8        92      117    
2098             Computer Hardware & Software     5.0        52       85    
2431                              IT Services     3.0       100      160    
880                                       NaN     3.6        81      141    
292                               IT Services     NaN        79      146    
105                       Sports & Recreation     3.9        84      113    
293                                       NaN     NaN        79      146    
1944                                      NaN     NaN        54      103    
377                               IT Services     4.8        94      164    

      Salary Estimate  DF  
400               NaN  DE  
193               NaN  DE  
2098              NaN  DE  
2431              NaN  DE  
880               NaN  DE  
292               NaN  DE  
105               NaN  DE  
293               NaN  DE  
1944              NaN  DE  
377               NaN  DE

In [10]:
dfDSJobs = pd.read_csv("900_DS_jobs_US_raw.csv")

dfDSJobs = dfDSJobs[["Job Title", "Job Description", "Company Name", "Location", 
                        "Size", "Founded", "Industry", "Rating", "Salary Estimate"]]

strCols = dfDSJobs.select_dtypes(['object']).columns
dfDSJobs[strCols] = dfDSJobs[strCols].apply(lambda x: x.str.strip())

# Note--Hard coded location changes and used code to determine row numbers of problematic locations: 
dfDSJobs.iloc[[7,118, 159, 174, 192, 199, 229, 279, 370],3]="Remote"
dfDSJobs.iloc[[125,182],3]="Pembroke Pines, FL"
dfDSJobs.iloc[274,3]="Raleigh, NC"
dfDSJobs.iloc[51,3]="Chicago, IL"
dfDSJobs.iloc[22,3]="Zeeland, MI"
dfDSJobs.iloc[[46, 459,517, 649],3]="New York, NY"
dfDSJobs.iloc[111,3]="Salt Lake City, UT"
dfDSJobs.iloc[[462,801],3]="Bellevue, WA"
dfDSJobs.iloc[[674, 492, 713, 864, 901],3]="Washington, DC"
dfDSJobs.iloc[568,3]="Stamford, CT"
dfDSJobs.iloc[[663,839],3]="San Francisco, CA"
dfDSJobs.iloc[735,3]="Seattle, WA"
dfDSJobs.iloc[48,3]="Holmdel, NJ"
dfDSJobs.iloc[[105, 132, 440, 579, 606],3]="Arlington, VA"
dfDSJobs.iloc[[219,223,352],3]="South Jordan, UT"
dfDSJobs.iloc[[448,620],3]="Los Angeles, CA"
dfDSJobs.iloc[[491,711,899],3]="Frederick, MD"
dfDSJobs.iloc[744,3]="Columbus, OH"

# Split Location into new columns--City and State and make city nan
dfDSJobs[["City", "State"]]= dfDSJobs["Location"].str.split(",", n = 1, expand = True)
dfDSJobs.loc[(~dfDSJobs["Location"].str.contains(",")), "State"]=dfDSJobs.loc[(~dfDSJobs["Location"].str.contains(",")),"City"]
dfDSJobs["State"]=dfDSJobs["State"].str.strip()
dfDSJobs.loc[(~dfDSJobs["Location"].str.contains(",")), "City"]=np.nan

postalKey = {"New Jersey": "NJ", 
                  "Virginia": "VA", 
                  "Maryland": "MD", 
                  "California": "CA", 
                  "Alabama": "AL", 
                  "Utah": "UT", 
                  "Ohio": "OH"}
dfDSJobs["State"].replace(postalKey, inplace=True)


# Creating a column for Remote work and make state nan
dfDSJobs.loc[(dfDSJobs["Location"]=="Remote"), "Remote"]="Yes"
dfDSJobs["Remote"].fillna(value = "Uncertain", axis=0, inplace=True)
dfDSJobs.loc[(dfDSJobs["Location"]=="Remote"), "State"]=np.nan

# Adding to column for Remote work from Job Description
dfDSJobs.loc[dfDSJobs["Job Description"].str.contains("Remote|remote"), "Remote"]= "Yes"

# Split Salary Estimate into SalaryMin and SalaryMax and replaced all Salary Estimate with NaN
dfDSJobs[["SalaryTest", "Salary"]] = dfDSJobs["Salary Estimate"].str.split("(", n = 1, expand = True)
dfDSJobs[["SalaryMin", "SalaryMax"]]= dfDSJobs["SalaryTest"].str.split("-", n = 1, expand = True)
dfDSJobs.drop(["SalaryTest", "Salary"], axis = 1, inplace = True)
dfDSJobs["Salary Estimate"] = np.NaN

#Removing the $ and the K from Salary Min and Max
dfDSJobs["SalaryMin"]=dfDSJobs["SalaryMin"].replace("[$K]","",regex=True)
dfDSJobs["SalaryMax"]=dfDSJobs["SalaryMax"].replace("[$K]","",regex=True)

# Created bin names for company sizes and used in dataframe
sizeKey = {"1 to 50 Employees": "Very Small", 
           "51 to 200 Employees": "Small",
          "201 to 500 Employees": "Medium-Small",
          "501 to 1000 Employees": "Medium",
          "1001 to 5000 Employees": "Medium-Large",
          "5001 to 10000 Employees": "Large",
          "10000+ Employees": "Very Large"}
dfDSJobs["Size"].replace(sizeKey, inplace=True)

# Removed rating from Company Name
dfDSJobs[["Company Name", "RateTest"]] = dfDSJobs["Company Name"].str.split("\n", n=1, expand = True)
dfDSJobs.drop("RateTest", axis = 1, inplace = True)

# Remove duplicate Job listing with same Job Descriptions
criteriaDS=["Company Name", "Job Title", "City", "State", "SalaryMin", "SalaryMax", "Job Description"]
DSduplicates=dfDSJobs[dfDSJobs.duplicated(criteriaDS)].sort_values(by=criteriaDS)
#testDS=DSduplicates.loc[DSduplicates["SalaryMin"].notnull()]
dfDSJobs=dfDSJobs[~dfDSJobs.duplicated(criteriaDS)]

# Dataframe Label
dfDSJobs["DF"]= "DS"

# Reordered Columns for Readability
dfDSJobs = dfDSJobs.reindex(columns = ["Job Title", "Job Description", "Company Name", "Location", "City", "State", 
                                        "Remote", "Size", "Founded", "Industry", "Rating", 
                                        "SalaryMin", "SalaryMax", "Salary Estimate", "DF"])

# Replace "unknown" and "-1" with NaN
dfDSJobs.replace({"Unknown": np.nan, "-1": np.nan, -1: np.nan}, inplace = True)
dfDSJobs.fillna(value=np.nan, axis=1, inplace=True)

print(DSduplicates.shape)
print(dfDSJobs.shape)
dfDSJobs.sample(10)

(8, 14)
(902, 15)


Job Title  \
247                                   SAP Data Analyst   
383                                     Data Scientist   
578                                     Data Scientist   
660  Translational Data Scientist, NIBR Translation...   
764               Sr.Data Scientist/Computer Scientist   
193                       HF Senior Engineer/Scientist   
635                                Lead Data Scientist   
155                                      Data Engineer   
116                          Machine Learning Engineer   
597                                     Data Scientist   

                                       Job Description          Company Name  \
247  POSITION PURPOSE:\n\nThe Data Analyst will be ...  Old World Industries   
383  We make small businesses more successful throu...              NorthOne   
578  About Alteryx\nAs a global leader in analytic ...               Alteryx   
660  20-Aug-2020\n\nJob ID\n300507BR\n{"QuestionNam...              Novartis   
764  Why choose between doing meaningful work and h...                 MITRE   
193  WR has a potential need of a Sr HF Engineer/Sc...            WR Systems   
635  Position: Lead Data Scientist\n\nLocation: Cin...          PatientPoint   
155  Job Description: The selected applicant will s...    AEgis Technologies   
116  Preferred Qualifications\nMasters degree in co...         Quicken Loans   
597  Progressive Leasing is seeking an experienced ...   Progressive Leasing   

                 Location              City State     Remote          Size  \
247        Northbrook, IL        Northbrook    IL  Uncertain  Medium-Small   
383     San Francisco, CA     San Francisco    CA  Uncertain    Very Small   
578            Boston, MA            Boston    MA  Uncertain  Medium-Large   
660         Cambridge, MA         Cambridge    MA  Uncertain    Very Large   
764            McLean, VA            McLean    VA  Uncertain         Large   
193           Fairfax, VA           Fairfax    VA  Uncertain  Medium-Small   
635        Cincinnati, OH        Cincinnati    OH  Uncertain  Medium-Small   
155  Colorado Springs, CO  Colorado Springs    CO  Uncertain  Medium-Small   
116           Detroit, MI           Detroit    MI  Uncertain    Very Large   
597    Salt Lake City, UT    Salt Lake City    UT  Uncertain  Medium-Large   

     Founded                                 Industry  Rating SalaryMin  \
247   1973.0                   Chemical Manufacturing     3.1       134   
383      NaN                                      NaN     4.2        48   
578   1997.0  Enterprise Software & Network Solutions     3.5        74   
660   1996.0                Biotech & Pharmaceuticals     4.0       115   
764   1958.0                         Federal Agencies     3.2       109   
193   1983.0                      Aerospace & Defense     3.7        98   
635   1987.0                  Advertising & Marketing     3.9        51   
155   1989.0                      Aerospace & Defense     4.1        59   
116   1985.0                                  Lending     3.8       150   
597   1999.0         Financial Transaction Processing     4.5        48   

    SalaryMax  Salary Estimate  DF  
247      213               NaN  DS  
383       80               NaN  DS  
578      127               NaN  DS  
660      181               NaN  DS  
764      153               NaN  DS  
193      160               NaN  DS  
635       92               NaN  DS  
155      101               NaN  DS  
116      169               NaN  DS  
597       89               NaN  DS

In [146]:
FullDataSet=pd.concat([df1, df2, dfGlassdoor, dfIndeed, dfLinkedIn, dfDataAnalyst, dfDataEngineer, dfDSJobs])
FullDataSet.reset_index(drop=True, inplace=True)

numCols = ["SalaryMin", "SalaryMax"]
FullDataSet[numCols] = FullDataSet[numCols].apply(lambda x: x.str.strip())

FullDataSet.loc[(FullDataSet["SalaryMax"].str.contains("Per Hour")==True),"Hourly"]=True
FullDataSet["Hourly"].fillna(value=False, axis=0, inplace=True)

# Replace "unknown" and "-1" and " " with NaN
FullDataSet.replace({"Unknown": np.nan, "-1": np.nan, -1: np.nan, "": np.nan}, inplace = True)
FullDataSet.fillna(value=np.nan, axis=1, inplace=True)

FullDataSet["SalaryMin"]=FullDataSet.SalaryMin.astype(float)
FullDataSet["SalaryMax"]=FullDataSet.SalaryMax.str.extract('(\d+)').astype(float)

# Reordered Columns for Consistency
FullDataSet = FullDataSet.reindex(columns = ["Job Title", "Job Description", "Company Name", "Location", "City", "State", 
                                        "Remote", "Size", "Founded", "Industry", "Rating", 
                                        "SalaryMin", "SalaryMax", "Salary Estimate", "Hourly", "Junior", "Senior", "DF"])

print(FullDataSet.shape)
FullDataSet.sample(20)

(27045, 18)


Job Title  \
17941                            Product Analyst - Rides   
6066                               Business Data Analyst   
26017                                  Software Engineer   
13970          Global Reporting and Analytics Consultant   
20342                          Data Scientist, Analytics   
1893                     In Process Analytical Scientist   
7458   ENGINEER - RESEARCH ENGINEER - SCIENTIST - KIN...   
7669                            Database Engineer (Temp)   
23496                         Security Data Analyst -CTJ   
15853  Senior Behavioral Scientist - 100% Remote or R...   
18612                                            Analyst   
12400                  Data Scientist - People Analytics   
9926                          Principal Proposal Analyst   
1713                             Analytical Scientist II   
22379          Senior Business Intelligence Data Analyst   
3451   AVP, Big Data and Machine Learning Solutions A...   
19239                         Lead Data Science Engineer   
4085                             Data Collection Analyst   
27014                                     Data Scientist   
17541          Data Scientist - Applied Machine Learning   

                                         Job Description  \
17941                                                NaN   
6066   Full Time - Lakewood, Colorado\n\nWe are seeki...   
26017  Job Category: Engineering\n\nWork Location: Ir...   
13970  Global Reporting and Analytics Consultant\n\n\...   
20342  What's Quibi?Launching next year, Quibi is the...   
1893   Company Description\nEurofins Scientific is an...   
7458   Join our Applied Power Division! Support techn...   
7669   Here at Daybreak, we make great games that bri...   
23496  Are you passionate about solving problems and ...   
15853  Senior Behavioral Scientist – 100% Remote or R...   
18612  B.S. or MBA, preferably in Marketing, Advertis...   
12400  Doctors Without Borders/Médecins Sans Frontièr...   
9926   Job DescriptionORGANIZATIONAL STRUCTUREBUSINES...   
1713   Company Overview\n\nOur growing and successful...   
22379  Summary and Essential Duties\n\n\nThe Senior B...   
3451   We are currently seeking an AVP, Big Data and ...   
19239  Highspot is seeking a lead data science engine...   
4085   Position Summary\n\nUnder the supervision of t...   
27014  Type of Requisition:\n\nRegular\n\nClearance L...   
17541  Transform and convert unstructured data set in...   

                                            Company Name  \
17941                                               Uber   
6066                                            MIRACORP   
26017                                           Pixentia   
13970                                     De Lage Landen   
20342                                              Quibi   
1893                                            Eurofins   
7458                        Southwest Research Institute   
7669                                      Daybreak Games   
23496                              Microsoft Corporation   
15853                                  Dell Technologies   
18612                                             Zenith   
12400  Doctors Without Borders | Médecins Sans Fronti...   
9926                                CIRCOR International   
1713                                   Quotient Sciences   
22379                                     Shamrock Foods   
3451                                       LPL Financial   
19239                                           Highspot   
4085                  Columbia University Medical Center   
27014            General Dynamics Information Technology   
17541                                              Apple   

                     Location                City State     Remote  \
17941       San Francisco, CA       San Francisco    CA  Uncertain   
6066             Lakewood, CO            Lakewood    CO  Uncertain   
26017              Irving, TX              Irving    T

In [147]:
FullDataSet.drop(index=[14054, 24631, 24654, 14061, 24661, 15438, 26236, 14504, 22651], axis=0, inplace=True)
FullDataSet.drop(index=[7031,7218,4612,7030,7205,4609,7198,10719, 4608], axis=0, inplace=True)

In [145]:
criteria=["Company Name", "Job Title", "City", "State", "SalaryMin", "SalaryMax", "Salary Estimate", "Hourly", "Job Description"]
duplicates=FullDataSet[FullDataSet.duplicated(subset=criteria, keep="first")].sort_values(by=criteria)
#test=duplicates.loc[duplicates["SalaryMin"].notnull()]

#print(test.shape)
#print(duplicates.shape)
#duplicates.head(20)

(0, 18)


Empty DataFrame
Columns: [Job Title, Job Description, Company Name, Location, City, State, Remote, Size, Founded, Industry, Rating, SalaryMin, SalaryMax, Salary Estimate, DF, Junior, Senior, Hourly]
Index: []

In [148]:
profile = pp.ProfileReport(FullDataSet, title = "Pandas Profiling Report", explorative = True)

profile

Summarize dataset:   0%|          | 0/32 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]